In [1]:
!pip install stable-baselines3[extra]
import stable_baselines3
!pip install keras-rl2

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 170 kB 5.6 MB/s 
     |████████████████████████████████| 1.5 MB 11.4 MB/s 
     |████████████████████████████████| 237 kB 37.5 MB/s 
     |████████████████████████████████| 1.6 MB 35.0 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 51 kB 6.0 MB/s 
  Created wheel for gym: filename=gym-0.21.0-py3-none-any.whl size=1616821 sha256=1372a43dc4029a19e654c4ec7d09bc52dc4baef4844d3d983815d5fc407bbcb2
  Stored in directory: /root/.cache/pip/wheels/76/ee/9c/36bfe3e079df99acf5ae57f4e3464ff2771b34447d6d2f2148
  Created wheel for AutoROM.accept-rom-license: filename=AutoROM.accept_rom_license-0.4.2-py3-none-any.whl size=441027 sha256=b9c0ef478fac01fa0864a24c4bcdc503feb57ca93e64997f314d2cc341ac9b38
  Stored in directory: /root/.cache/pip/whe

In [2]:
import gym
import random 
import time
import matplotlib.pyplot as plt
import matplotlib
import warnings
import numpy as np
from IPython.display import clear_output
from tqdm import tqdm_notebook
from tensorflow import keras
import tensorflow as tf
import datetime
from collections import deque
import cv2
import stable_baselines3.common.atari_wrappers as atari_wrappers

In [3]:
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D
from tensorflow.keras.layers import MaxPool2D
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam

In [4]:
# env = gym.make("FrozenLake-v1")
# env = gym.make('FrozenLake-v1', desc=None, map_name="8x8", is_slippery=False)
env = gym.make('FrozenLake-v1', map_name="8x8")
#Initialize environment. v4 means no action repeat
# env = gym.make('PongNoFrameskip-v4')
env.observation_space
# env.unwrapped.
actions = env.action_space.n
actions

4

In [5]:
my_world = [
    'FFFS',
    'FFFF',
    'FFFF',
    'FGFG',
]

env = gym.make("FrozenLake-v1", desc=my_world, is_slippery=False)

# env = gym.make('FrozenLake-v1', map_name="8x8")

In [6]:
env.reset()
# env.step(0)
env.render()



FFFS
FFFF
FFFF
FGFG


In [7]:
def print_action_meaning(action):
  if action == 0:
    print('Move LEFT')
  elif action == 1:
    print('Move DOWN')
  elif action == 2:
    print('Move RIGHT')
  elif action == 3:
    print('Move UP')

In [8]:
def random_walk_test():
  # !python -m atari_py.import_roms ROMS
  episodes = 5
  for episode in range (0, 5):
    state = env.reset()
    done = False
    score = 0

    while not done:
      env.render()
      action = random.choice([0,1,2,3])
      n_state, reward, done, info = env.step(action)
      score+=reward
  
  print('Episode: {}, Score: {}'.format(episode, score))
  env.close()

In [37]:
class Agent:
    def __init__(self, state_size, action_size):
        self.memory = deque(maxlen=2500)
        self.learning_rate=0.001
        self.explore_prob=0.5
        self.max_eps=1
        self.min_eps=0.01
        self.discount_factor = 0.001/3
        self.gamma=0.9
        self.state_size= state_size
        self.action_size= action_size
        self.explore_prob_lst=[]
        self.model = self.initialize_NN()

    def initialize_NN(self):
        model=Sequential()
        model.add(Dense(32, input_dim=self.state_size, activation='relu'))
        model.add(Dense(32, activation='relu'))
        model.add(Dense(self.action_size, activation='linear'))
        model.compile(loss='mse', optimizer=Adam(learning_rate=self.learning_rate))
        return model

    def add_memory(self, new_state, reward, done, state, action):
        self.memory.append((new_state, reward, done, state, action))

    def action(self, state):
        if np.random.rand() > self.explore_prob:
            return np.random.randint(0,4)
        # if train:
        #     return np.random.randint(0,4)
        return np.argmax(self.model.predict(state))

    def pred(self, state):
        return np.argmax(self.model.predict(state))

    def replay(self,batch_size):
        minibatch=random.sample(self.memory, batch_size)
        for new_state, reward, done, state, action in minibatch:
            target= reward
            if not done:
                target=reward + self.gamma* np.amax(self.model.predict(new_state))
            target_f= self.model.predict(state)
            target_f[0][action]= target
            self.model.fit(state, target_f, epochs=1, verbose=0)

        if self.explore_prob > self.min_eps:
            self.explore_prob=(self.max_eps - self.min_eps) * np.exp(-self.discount_factor*episode) + self.min_eps

        self.explore_prob_lst.append(self.explore_prob)


In [35]:
train_episodes=1000
test_episodes=100
max_steps=500
state_size = env.observation_space.n
action_size = env.action_space.n
batch_size=4
print('Number of states: {}, number of actions: {}'.format(state_size, action_size))


Number of states: 16, number of actions: 4


In [36]:
agent=Agent(state_size, action_size)

train = True

rewards=[]
for episode in range(train_episodes):
    state = env.reset()
    state_arr = np.zeros(state_size)
    state_arr[state] = 1
    state = np.reshape(state_arr, [1, state_size])
    reward = 0
    done = False
    for t in range(max_steps):
        # env.render()
        action = agent.action(state)
        new_state, reward, done, info = env.step(action)
        new_state_arr = np.zeros(state_size)
        new_state_arr[new_state] = 1
        new_state = np.reshape(new_state_arr, [1, state_size])
        agent.add_memory(new_state, reward, done, state, action)
        state= new_state

        if done:
            # print(f'Episode: {episode:4}/{train_episodes} and step: {t:4}. Eps: {float(agent.explore_prob):.2}, reward {reward}')
            if reward == 1:
              print ('reward is 1')
            break

    rewards.append(reward)

    if len(agent.memory)> batch_size:
        agent.replay(batch_size)

print(' Training score = ', round(100*np.mean(rewards),1), '%')

1/1 [==============================] - 0s 21ms/step
reward is 1
1/1 [==============================] - 0s 22ms/step


KeyboardInterrupt: ignored

In [32]:
my_map = [
    'FFFS',
    'FFFF',
    'FFFF',
    'GFFF',
]

env = gym.make("FrozenLake-v1", desc=my_map, is_slippery=False)

# env = gym.make('FrozenLake-v1', map_name="8x8")

In [33]:
# test
test_results=[]
train = False
test_episodes = 10
for episode in range(test_episodes):
    state = env.reset()
    state_arr=np.zeros(state_size)
    state_arr[state] = 1
    state= np.reshape(state_arr, [1, state_size])
    done = False
    reward=0
    state_lst = []
    state_lst.append(state)
    print('******* EPISODE ',episode, ' *******')

    for step in range(max_steps):
        action = agent.pred(state)
        print_action_meaning(action)
        new_state, reward, done, info = env.step(action)
        new_state_arr = np.zeros(state_size)
        new_state_arr[new_state] = 1
        new_state = np.reshape(new_state_arr, [1, state_size])
        state = new_state
        state_lst.append(state)
        if done:
            print(reward)
            # env.render()
            break

    test_results.append(reward)
env.close()
print('Validation score= ', int(100*np.mean(test_results)))

******* EPISODE  0  *******
1/1 [==============================] - 0s 27ms/step
Move LEFT
1/1 [==============================] - 0s 25ms/step
Move LEFT
1/1 [==============================] - 0s 26ms/step
Move LEFT
1/1 [==============================] - 0s 31ms/step
Move DOWN
1/1 [==============================] - 0s 20ms/step
Move DOWN
1/1 [==============================] - 0s 21ms/step
Move DOWN
1.0
******* EPISODE  1  *******
1/1 [==============================] - 0s 19ms/step
Move LEFT
1/1 [==============================] - 0s 21ms/step
Move LEFT
1/1 [==============================] - 0s 31ms/step
Move LEFT
1/1 [==============================] - 0s 24ms/step
Move DOWN
1/1 [==============================] - 0s 25ms/step
Move DOWN
1/1 [==============================] - 0s 27ms/step
Move DOWN
1.0
******* EPISODE  2  *******
1/1 [==============================] - 0s 18ms/step
Move LEFT
1/1 [==============================] - 0s 24ms/step
Move LEFT
1/1 [==============================] - 0